## Convert video into frames

In [ ]:
# If the library isn't insalled, run the following command
# !pip install opencv-python

In [5]:
## Import the library
import cv2
import os
import glob

In [6]:
HOME = os.path.split(os.getcwd())[0]
print(HOME)

d:\Code\CowId


In [7]:
## Function that converts video into frames by taking the video path as input

def video_to_frames(input_loc, output_loc, filename):

    # Create folder if not exists
    if not os.path.exists(output_loc):
        os.makedirs(output_loc)
        
    vidcap = cv2.VideoCapture(input_loc)
    success, image = vidcap.read()
    count = 0
    while success:
        # For raw videos, use the one with if
        if (count % 2 == 0): cv2.imwrite(f'{output_loc}/{filename}-{str(count).zfill(8)}.jpg', image)  
        # cv2.imwrite(f'{output_loc}/{filename}-{str(count).zfill(8)}.jpg', image)     # save frame as JPEG file      
        success,image = vidcap.read()
        print('Read a new frame: ', count)
        count += 1

To convert a single video

In [8]:
def process_all_videos(video_folder, output_folder):
    # Loop through all the videos in the folder
    for filename in os.listdir(video_folder):
        if filename.endswith(".mp4"):  # check if it's a .mp4 video
            # Get the base name (i.e., name without extension) to use as output name
            base_name = os.path.splitext(filename)[0]

            video_path = os.path.join(video_folder, filename)
            frames_output_path = os.path.join(output_folder, base_name)

            # apply function on each video
            video_to_frames(video_path, frames_output_path, base_name)

To convert all videos from a directory

In [9]:
process_all_videos(os.path.join(HOME, 'data', 'videos_230611'), os.path.join(HOME, 'data', 'videos_frames_2'))

Read a new frame:  0
Read a new frame:  1
Read a new frame:  2
Read a new frame:  3
Read a new frame:  4
Read a new frame:  5
Read a new frame:  6
Read a new frame:  7
Read a new frame:  8
Read a new frame:  9
Read a new frame:  10
Read a new frame:  11
Read a new frame:  12
Read a new frame:  13
Read a new frame:  14
Read a new frame:  15
Read a new frame:  16
Read a new frame:  17
Read a new frame:  18
Read a new frame:  19
Read a new frame:  20
Read a new frame:  21
Read a new frame:  22
Read a new frame:  23
Read a new frame:  24
Read a new frame:  25
Read a new frame:  26
Read a new frame:  27
Read a new frame:  28
Read a new frame:  29
Read a new frame:  30
Read a new frame:  31
Read a new frame:  32
Read a new frame:  33
Read a new frame:  34
Read a new frame:  35
Read a new frame:  36
Read a new frame:  37
Read a new frame:  38
Read a new frame:  39
Read a new frame:  40
Read a new frame:  41
Read a new frame:  42
Read a new frame:  43
Read a new frame:  44
Read a new frame:  4

### Prediction with YOLO

In [10]:
from ultralytics import YOLO
from PIL import Image
import os

HOME = os.path.split(os.getcwd())[0]
print(HOME)

d:\Code\CowId


In [11]:
model = YOLO(f"{HOME}/data/yolo_models/train11/weights/best.pt")

img_dir = os.path.join(HOME, 'data', 'videos_frames_2')

output_dir = os.path.join(HOME, 'data', 'yolo_output_2')

def expand_rectangle_to_square(x1, y1, x2, y2):
    width = abs(x2 - x1)
    height = abs(y2 - y1)
    size = max(width, height)
    center_x = (x1 + x2) / 2
    center_y = (y1 + y2) / 2
    new_x1 = center_x - size / 2
    new_y1 = center_y - size / 2
    new_x2 = center_x + size / 2
    new_y2 = center_y + size / 2
    return new_x1, new_y1, new_x2, new_y2

def crop_to_square(image_path, x1, y1, x2, y2):
    image = Image.open(image_path)
    cropped_image = image.crop((x1, y1, x2, y2))
    cropped_image = cropped_image.resize((250, 250))
    return cropped_image

In [16]:
def process_images(img_dir, output_dir):
    for root, dirs, files in os.walk(img_dir):
        for filename in files:
            if filename.endswith(".jpg"):
                img_path = os.path.join(root, filename)
                res = model(img_path, conf=0.75)
                boxes = res[0].boxes.xyxy.tolist()
                cow_number = 0
                for inner_list in boxes:
                    cow_number += 1
                    x1, y1, x2, y2 = inner_list
                    x1, y1, x2, y2 = expand_rectangle_to_square(x1, y1, x2, y2)
                    cropped_image = crop_to_square(img_path, x1, y1, x2, y2)
                    output_filename = f"{os.path.splitext(filename)[0]}-{cow_number}.jpg"
                    print(output_dir)
                    if not os.path.exists(output_dir):
                        os.makedirs(output_dir)
                    output_path = os.path.join(output_dir, output_filename)
                    cropped_image.save(output_path)

In [17]:
process_images(img_dir, output_dir)


image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000000.jpg: 384x640 (no detections), 39.5ms
Speed: 1.0ms preprocess, 39.5ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)



image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000002.jpg: 384x640 (no detections), 38.7ms
Speed: 2.5ms preprocess, 38.7ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000004.jpg: 384x640 (no detections), 40.1ms
Speed: 1.0ms preprocess, 40.1ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000006.jpg: 384x640 (no detections), 54.2ms
Speed: 2.0ms preprocess, 54.2ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000008.jpg: 384x640 (no detections), 58.3ms
Speed: 5.5ms preprocess, 58.3ms inference, 12.2ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000010.jpg: 384x640 (no detections), 36.7ms
Speed: 3.5ms preprocess, 36.7ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

imag

d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2


image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000050.jpg: 384x640 1 cow, 6.0ms
Speed: 0.0ms preprocess, 6.0ms inference, 2.1ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000052.jpg: 384x640 1 cow, 4.0ms
Speed: 0.0ms preprocess, 4.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000054.jpg: 384x640 1 cow, 4.0ms
Speed: 0.0ms preprocess, 4.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000056.jpg: 384x640 1 cow, 3.0ms
Speed: 1.0ms preprocess, 3.0ms inference, 3.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000058.jpg: 384x640 1 cow, 5.1ms
Speed: 0.0ms preprocess, 5.1ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T1VA\T1VA-00000060.j

d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2


...

Speed: 0.0ms preprocess, 8.0ms inference, 3.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004784.jpg: 384x640 1 cow, 6.5ms
Speed: 4.0ms preprocess, 6.5ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004786.jpg: 384x640 1 cow, 8.6ms
Speed: 1.0ms preprocess, 8.6ms inference, 1.5ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004788.jpg: 384x640 1 cow, 6.5ms
Speed: 1.0ms preprocess, 6.5ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004790.jpg: 384x640 1 cow, 7.5ms
Speed: 1.0ms preprocess, 7.5ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004792.jpg: 384x640 1 cow, 6.5ms
Speed: 1.0ms preprocess, 6.5ms inference, 5.0ms postprocess per i

d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2
d:\Code\CowId\data\yolo_output_2


image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004798.jpg: 384x640 1 cow, 7.5ms
Speed: 1.0ms preprocess, 7.5ms inference, 4.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004800.jpg: 384x640 (no detections), 6.1ms
Speed: 2.0ms preprocess, 6.1ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004802.jpg: 384x640 (no detections), 6.7ms
Speed: 1.0ms preprocess, 6.7ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004804.jpg: 384x640 (no detections), 8.5ms
Speed: 0.8ms preprocess, 8.5ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004806.jpg: 384x640 (no detections), 7.2ms
Speed: 1.0ms preprocess, 7.2ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\d

d:\Code\CowId\data\yolo_output_2


Speed: 1.0ms preprocess, 7.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004818.jpg: 384x640 (no detections), 7.0ms
Speed: 1.0ms preprocess, 7.0ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004820.jpg: 384x640 (no detections), 10.5ms
Speed: 1.0ms preprocess, 10.5ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004822.jpg: 384x640 (no detections), 7.7ms
Speed: 0.0ms preprocess, 7.7ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004824.jpg: 384x640 (no detections), 9.5ms
Speed: 0.0ms preprocess, 9.5ms inference, 1.0ms postprocess per image at shape (1, 3, 640, 640)

image 1/1 D:\Code\CowId\data\videos_frames_2\T2VB\T2VB-00004826.jpg: 384x640 (no detections), 10.1ms
Speed: 1.0ms